In [ ]:
# Check the graphics card
!nvidia-smi

Fri Mar 10 11:50:53 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.85.12    Driver Version: 525.85.12    CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA A100-SXM...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   30C    P0    50W / 400W |      0MiB / 40960MiB |      0%      Default |
|                               |                      |             Disabled |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
#@title clone github repository
!git clone https://github.com/ThePioneerJP/so-vits-svc -b 4.0
#!git clone https://github.com/svc-develop-team/so-vits-svc -b 4.0


Cloning into 'so-vits-svc'...
remote: Enumerating objects: 305, done.
remote: Counting objects: 100% (87/87), done.
remote: Compressing objects: 100% (68/68), done.
remote: Total 305 (delta 29), reused 23 (delta 4), pack-reused 218
Receiving objects: 100% (305/305), 8.03 MiB | 17.92 MiB/s, done.
Resolving deltas: 100% (116/116), done.


In [ ]:
#@title install dependencies
%cd /content/so-vits-svc
!pip install pyproject-toml
!pip install pyworld praat-parselmouth #fairseq, won't work

/content/so-vits-svc
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 214.4/214.4 KB 18.2 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 100.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 102.2 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.9/118.9 KB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 269.6/269.6 KB 29.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.8/123.8 KB 276.7 

In [ ]:
#@title Install fairseq manually, as pip won't work. Make sure to move fairseq/fairseq directly below sovits folder before starting the training/inference.
#!rm -r /content/so-vits-svc/fairseq
!git clone https://github.com/pytorch/fairseq
%cd fairseq
!pip install --editable ./

Cloning into 'fairseq'...
remote: Enumerating objects: 34534, done.
remote: Total 34534 (delta 0), reused 0 (delta 0), pack-reused 34534
Receiving objects: 100% (34534/34534), 24.06 MiB | 17.61 MiB/s, done.
Resolving deltas: 100% (25109/25109), done.
/content/so-vits-svc/fairseq
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Obtaining file:///content/so-vits-svc/fairseq
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Using cached hydra_core-1.0.7-py3-none-any.whl (123 kB)
  Using cached omegaconf-2.0.6-py3-none-any.whl (36 kB)
  Using cached sacrebleu-2.3.1-py3-none-any.whl (118 kB)
  Using cached bitarray-2.7.3-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (269 kB)
  Using cached antlr4_python3_runtime-4.8-py3-none-any.whl
  Using cached portalocker-2.7.0-py2.py3-none-any.whl

In [ ]:
#@title Download necessary model files
# Source warehouse address: [contentvec](https://github.com/auspicious3000/contentvec)
# Model original download link: [checkpoint_best_legacy_500.pt](https://ibm.box.com/s/z1wgl1stco8ffooyatzdwsqn2psd9lrr)
# Since the source network disk cannot provide http direct links, according to the mit protocol, the model is redistributed to provide download direct links
%cd /content/so-vits-svc
!wget -P hubert/ https://huggingface.co/ThePioneer/NaturalGirlyVoice/resolve/main/checkpoint_best_legacy_500.pt -O hubert/checkpoint_best_legacy_500.pt

# Dataset preprocessing

In [ ]:
#@title Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
#@title backup everything (to protect from deletion)
!cp -r "/content/so-vits-svc" "/content/drive/MyDrive/so-vits-svc-backup"

This processing script can preprocess multiple speakers at one time, and generate multi-speaker filelists and corresponding configuration files

Just put your dataset into the dataset_raw directory according to the following file structure


```
dataset_raw
├───speaker0
│   ├───xxx1-xxx1.wav
│   ├───...
│   └───Lxx-0xx8.wav
└───speaker1
    ├───xx2-0xxx2.wav
    ├───...
    └───xxx7-xxx007.wav
```

In [ ]:
#@title Load the packaged dataset from Google Cloud Disk for preprocessing
#@markdown **The data set of sovits3.0 no longer needs a specific file structure. Put all the wav files of the data set in the same folder, compress them into zip and upload them to Google Cloud Disk. This processing script can preprocess multiple Dataset, when processing multiple datasets, please decompress each dataset in turn**

#@markdown Dataset name (**character’s English/Pinyin name**, which is the same as when creating the data folder; without zip.)
DATASETNAME = "Ver0"  #@param {type:"string"}
#@markdown Compressed package path (Google disk path, don’t change this if you pass it to dataset, create a new one if there is no dataset folder)
#ZIP_PATH = "/content/drive/MyDrive/dataset/"  #@param {type:"string"}
#ZIP_NAME = ZIP_PATH + DATASETNAME

!cp -r /content/drive/MyDrive/diff-svc_dataset_wav_denoised /content/so-vits-svc/dataset_raw

In [ ]:
#@title Resample to 44100hz
%cd /content/so-vits-svc
!python resample.py

In [ ]:
#@title Divide the training set Generate configuration files
!python preprocess_flist_config.py

In [ ]:
#@title generate hubert and f0
%cd /content/so-vits-svc
!pip install pyworld
!python preprocess_hubert_f0.py

In [ ]:
#@title At this point, the preprocessing of the data set is completed, and the data set and related files are saved to the dataset folder of Google Cloud Disk, which is convenient for the next training
#Compress the dataset folder
!zip -r dataset.zip /content/so-vits-svc/dataset
#@markdown Customize the name of the dataset folder under the dataset folder of Google Cloud Disk to avoid confusion
dataset_name_drive = "Ver0_sovits4"  #@param {type:"string"}
DATASET_PATH_DRIVE = "/content/drive/MyDrive/dataset/" + dataset_name_drive
!mkdir -p {DATASET_PATH_DRIVE}

!cp /content/so-vits-svc/dataset.zip "{DATASET_PATH_DRIVE}"
!cp configs/config.json "{DATASET_PATH_DRIVE}"
!cp filelists/train.txt "{DATASET_PATH_DRIVE}"
!cp filelists/val.txt "{DATASET_PATH_DRIVE}"

In [ ]:
#@title If the data set has been preprocessed, you can skip the preprocessing part and decompress the processed data and configuration files directly from the cloud disk
#@markdown Load the preprocessed data set from Google Cloud Disk, the folder name is the same as you entered when you backed up
back_up_name = "Ver0_sovits4"  #@param {type:"string"}
BACK_UP_DATASET_PATH = "/content/drive/MyDrive/dataset/" + back_up_name
!unzip {BACK_UP_DATASET_PATH}/dataset.zip -d /
!cp {BACK_UP_DATASET_PATH}/config.json /content/so-vits-svc/configs/config.json 
!cp {BACK_UP_DATASET_PATH}/val.txt filelists/val.txt
!cp {BACK_UP_DATASET_PATH}/train.txt filelists/train.txt


# Copy the record points saved on the cloud disk
# !cp /content/drive/MyDrive/G_800.pth logs/48k/
# !cp /content/drive/MyDrive/D_800.pth logs/48k/

# Training

In [ ]:
#@title  Choose whether to save the trained model to Google Cloud Disk and whether to use the pre-model. It also works to continue training from the last saved point.

#@markdown **Save the trained model file to Google Cloud Disk. After checking, you also need to check and execute when resuming training**
Save_to_drive = True #@param {type:"boolean"}
if Save_to_drive:
  !rm -rf /content/so-vits-svc/logs/44k
  !mkdir -p /content/drive/MyDrive/44k
  !ln -s /content/drive/MyDrive/44k /content/so-vits-svc/logs/44k

#@markdown **Download the pre-model for the first training and continue training after using the record points saved by yourself, no need to download again**

#@markdown **Use the pre-model, check the box below to automatically download and enable**
pre_pth = False #@param {type:"boolean"}
if pre_pth:
  !wget -P logs/44k/ https://huggingface.co/ThePioneer/NaturalGirlyVoice/resolve/main/G_0.pth
  !wget -P logs/44k/ https://huggingface.co/ThePioneer/NaturalGirlyVoice/resolve/main/D_0.pth


In [ ]:
#@title  Start training

#@markdown **start training**

#@markdown **Enable tensorboard to visualize data**
tensorboard_on = False #@param {type:"boolean"}
if tensorboard_on:
  %load_ext tensorboard
  %tensorboard --logdir logs/44k

!python train.py -c configs/config.json -m 44k


In [ ]:
#@title Manually back up the trained model files to Google Cloud Disk
#@markdown You need to check the file name of the model under the /content/so-vits-svc/logs/44k/ folder by yourself, and manually modify the file name at the end of the command below
!mv /content/so-vits-svc/logs/44k/G_1000.pth /content/drive/MyDrive
!mv /content/so-vits-svc/logs/44k/D_1000.pth /content/drive/MyDrive

# Inference

In [ ]:
#@title install necessary packages for inference
%cd /content/so-vits-svc
#!pip install parselmouth
!pip install praat-parselmouth

In [ ]:
#@title Synthetic Audio (Inference)
#@markdown needs to upload the audio to the so-vits-svc/raw folder, and then set the model path, configuration file path, and synthesized audio name

!python inference_main.py -m "/content/drive/MyDrive/44k/G_100000.pth" -c "configs/config.json" -n "君の知らない物語-src.wav" -s Ver0 -t 0 -wf wav
